## Evaluating the suitability filter on CivilComments

In [1]:
import importlib
import random

import numpy as np
import pandas as pd
import torch

from suitability.datasets.wilds import get_wilds_dataset, get_wilds_model
from suitability.filter import suitability_efficient

importlib.reload(suitability_efficient)

from suitability.filter.suitability_efficient import SuitabilityFilter, get_sf_features

# Set seeds for reproducibility
random.seed(32)
np.random.seed(32)

# SPLIT SUBSET EVALS

In [2]:
import pickle
import random

import numpy as np
import pandas as pd
import torch
from tqdm import tqdm

from suitability.filter.suitability_efficient import SuitabilityFilter
from suitability.filter.tests import non_inferiority_ttest

# Set seeds for reproducibility
random.seed(32)
np.random.seed(32)

# Configuration
data_name = "civilcomments"
root_dir = "/mfsnic/projects/suitability/"
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load the model
algorithm = "ERM"
model_type = "last"
seed = 2

# Load the features
feature_cache_file = (
    f"suitability/results/features/{data_name}_{algorithm}_{model_type}_{seed}.pkl"
)
with open(feature_cache_file, "rb") as f:
    feature_dict = pickle.load(f)

# Load the split indices
split_cache_file = f"suitability/results/split_indices/{data_name}.pkl"
with open(split_cache_file, "rb") as f:
    split_dict = pickle.load(f)

# Define suitability filter and experiment parameters
classifiers = [
    "logistic_regression"
]  # "logistic_regression", "svm", "random_forest", "gradient_boosting", "mlp", "decision_tree"]
margins = [0, 0.005, 0.01, 0.05]
normalize = True
calibrated = True
sf_results = []
direct_testing_results = []
feature_subsets = [
    [0],
    [1],
    [2],
    [3],
    [4],
    [5],
    [6],
    [7],
    [8],
    [9],
    [10],
    [11],
    # [4, 11],
    # [4, 11, 8],
    # [4, 11, 8, 6],
    # [4, 11, 8, 6, 2],
    # [4, 11, 8, 6, 2, 1],
    # [4, 11, 8, 6, 2, 1, 0],
    # [4, 11, 8, 6, 2, 1, 0, 7],
    # [4, 11, 8, 6, 2, 1, 0, 7, 3],
    # [4, 11, 8, 6, 2, 1, 0, 7, 3, 10],
    # [4, 11, 8, 6, 2, 1, 0, 7, 3, 10, 5],
    [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11],
]
num_fold_arr = [15]

# Main loop
for user_split_name, user_filter in tqdm(split_dict.keys()):
    print(f"Evaluating user split: {user_split_name} with filter {user_filter}")

    # Get user split indices
    user_split_indices = split_dict[(user_split_name, user_filter)]

    # Get user split features and correctness
    all_features, all_corr = feature_dict[user_split_name]
    user_features = all_features[user_split_indices]
    user_corr = all_corr[user_split_indices]
    user_size = len(user_corr)
    user_acc = np.mean(user_corr)

    # Re-partition remaining data into folds
    remaining_indices = np.setdiff1d(np.arange(len(all_corr)), user_split_indices)
    remaining_features = all_features[remaining_indices]
    remaining_corr = all_corr[remaining_indices]
    if user_split_name == "val":
        other_split_name = "test"
    elif user_split_name == "test":
        other_split_name = "val"
    else:
        raise ValueError(f"Invalid split name: {user_split_name}")
    additional_features, additional_corr = feature_dict[other_split_name]
    source_features = np.concatenate([remaining_features, additional_features], axis=0)
    source_corr = np.concatenate([remaining_corr, additional_corr], axis=0)

    for num_folds in num_fold_arr:
        source_fold_size = len(source_corr) // num_folds
        indices = np.arange(len(source_corr))
        np.random.shuffle(indices)
        fold_indices = [
            indices[i * source_fold_size : (i + 1) * source_fold_size]
            for i in range(num_folds)
        ]

        for i, reg_indices in enumerate(fold_indices):
            reg_features = source_features[reg_indices]
            reg_corr = source_corr[reg_indices]
            reg_size = len(reg_corr)
            reg_acc = np.mean(reg_corr)

            for j, test_indices in enumerate(fold_indices):
                if i == j:
                    continue
                test_features = source_features[test_indices]
                test_corr = source_corr[test_indices]
                test_size = len(test_corr)
                test_acc = np.mean(test_corr)

                for classifier in classifiers:
                    for feature_subset in feature_subsets:
                        suitability_filter = SuitabilityFilter(
                            test_features,
                            test_corr,
                            reg_features,
                            reg_corr,
                            device,
                            normalize=normalize,
                            feature_subset=feature_subset,
                        )
                        suitability_filter.train_classifier(
                            calibrated=calibrated, classifier=classifier
                        )

                        for margin in margins:
                            # Test suitability filter
                            sf_test = suitability_filter.suitability_test(
                                user_features=user_features, margin=margin
                            )
                            p_value = sf_test["p_value"]
                            ground_truth = user_acc >= test_acc - margin

                            sf_results.append(
                                {
                                    "data_name": data_name,
                                    "algorithm": algorithm,
                                    "seed": seed,
                                    "model_type": model_type,
                                    "normalize": normalize,
                                    "calibrated": calibrated,
                                    "margin": margin,
                                    "reg_fold": i,
                                    "reg_size": reg_size,
                                    "reg_acc": reg_acc,
                                    "test_fold": j,
                                    "test_size": test_size,
                                    "test_acc": test_acc,
                                    "user_split": user_split_name,
                                    "user_filter": user_filter,
                                    "user_size": user_size,
                                    "user_acc": user_acc,
                                    "p_value": p_value,
                                    "ground_truth": ground_truth,
                                    "classifier": classifier,
                                    "feature_subset": feature_subset,
                                    "acc_diff": user_acc - test_acc,
                                    "acc_diff_adjusted": user_acc + margin - test_acc,
                                }
                            )

                            # Run non-inferiority test on features directly
                            if (
                                len(feature_subset) == 1
                                and margin == 0
                                and classifier == "logistic_regression"
                                and (j == 0 or (i == 0 and j == 1))
                            ):
                                test_feature_subset = test_features[:, feature_subset].flatten()
                                user_feature_subset = user_features[:, feature_subset].flatten()
                                test_1 = non_inferiority_ttest(
                                    test_feature_subset,
                                    user_feature_subset,
                                    increase_good=True,
                                )
                                test_2 = non_inferiority_ttest(
                                    test_feature_subset,
                                    user_feature_subset,
                                    increase_good=False,
                                )
                                direct_testing_results.append(
                                    {
                                        "data_name": data_name,
                                        "algorithm": algorithm,
                                        "seed": seed,
                                        "model_type": model_type,
                                        "test_fold": j,
                                        "test_size": test_size,
                                        "test_acc": test_acc,
                                        "user_split": user_split_name,
                                        "user_filter": user_filter,
                                        "user_size": user_size,
                                        "user_acc": user_acc,
                                        "p_value_increase_good": test_1["p_value"],
                                        "p_value_decrease_good": test_2["p_value"],
                                        "ground_truth": ground_truth,
                                        "feature_subset": feature_subset,
                                        "acc_diff": user_acc - test_acc,
                                    }
                                )


# Save results
sf_evals = pd.DataFrame(sf_results)
sf_evals.to_csv(
    f"suitability/results/sf_evals/erm/civilcomments_sf_results_id_subsets_{algorithm}_{model_type}_{seed}.csv",
    index=False,
)
direct_testing_evals = pd.DataFrame(direct_testing_results)
direct_testing_evals.to_csv(
    f"suitability/results/sf_evals/erm/civilcomments_direct_testing_results_id_subsets_{algorithm}_{model_type}_{seed}.csv",
    index=False,
)


  0%|                                                                                                               | 0/16 [00:00<?, ?it/s]

Evaluating user split: val with filter {'sensitive': 'male'}


/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_n

Evaluating user split: val with filter {'sensitive': 'female'}


/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_n

...

/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_n

Evaluating user split: test with filter {'sensitive': 'black'}


/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_n

Evaluating user split: test with filter {'sensitive': 'white'}


/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_nan_policy.py:531: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, **kwds)
/mfsnic/u/apouget/envs/test/lib/python3.11/site-packages/scipy/stats/_axis_n